In [2]:
# Dependencies and Setup
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import time
from pprint import pprint
import scipy.stats as st
import os.path
from os import path
import json

# Incorporated citipy to determine city based on latitude and longitude
from citipy import citipy

# Output File (CSV)
output_data_players_Titled = "output_data/players_Titled.csv"

country_filepath = "resources/countries.csv"

titled_players_type = ["GM","WGM","IM","WIM","FM","WFM","NM","WNM","CM","WCM"]

# Range of latitudes and longitudes
# lat_range = (-90, 90)
# lng_range = (-180, 180)

In [3]:
# function get usernames by country, pass country code and output file
# returns list of usernames for specific country and saves output file to csv
def get_usernames_country(country, output_file):
    try: 
        # country code # countries list resource https://en.wikipedia.org/wiki/ISO_3166-1_alpha-2
        # country = "RU" # RUSSIA = RU

        query_url = f"https://api.chess.com/pub/country/{country}/players"

        print(f"Fetching player list for country {country}")

        
        # Get player usernames for country
        username_response = requests.get(query_url)
        username_json = username_response.json()        
        # username_json
        
        usernames = []
        for username in username_json["players"]:
            usernames.append(username)

        player_dict = {    
            "username":usernames
        }
        chessplayers_df = pd.DataFrame(player_dict)
        chessplayers_df.to_csv(output_file, index=True,index_label="player_index")          
        
        return chessplayers_df                
    except: 
        print("Unexpected error.")

In [4]:
# pass list of player types
# return player data json for each type of player 
def get_titledplayers_api(playertypes):
    url = "https://api.chess.com/pub/titled/"
    
    i = 0        
    players_data = []
    
    for playertype in playertypes:
        print(f"Index {str(i)} fetching player list for titled player type {playertype}")
    
        # Build query URL
        query_url = f"{url}{playertype}"

        # increment index counter
        i += 1

        # Get weather data    
        playertype_response = requests.get(query_url)
        playertype_json = playertype_response.json()
        players_data.append(playertype_json)        
        # time.sleep()    
        
    return players_data

In [5]:
# pass list of players 
# return player_data json player details
def get_playerdata_api(player_usernames):
    url = "https://api.chess.com/pub/player/"
    
    i = 0        
    player_data = []
    
    for player_username in player_usernames:
        print(f"Index {str(i)} fetching player data for player {player_username}")
    
        # Build query URL
        query_url = f"{url}{player_username}"

        # increment index counter
        i += 1

        # Get player data    
        try:
            player_response = requests.get(query_url)
            player_json = player_response.json()
            player_data.append(player_json)        
            # time.sleep(1)    
        except:
            print("unexpected error")
            
    return player_data

In [6]:
# pass playerdata json
# return dataframe with player details
def get_player_dataframe(playerdata):                
    player_id = []
    player_username = []
    title = []
    followers = []
    country = []
    location = []
    last_online = []
    joined = []
    status = []
    is_streamer = []

    i = 0

    for player in playerdata: 
        try:            
            username = player["username"]
            print(f"Index {i} processing username {username}")
            player_id.append(player["player_id"])
            player_username.append(username)
            if "title" in player.keys():
                title.append(player["title"])
            else:
                title.append("")          
            followers.append(player["followers"])        
            country.append(player["country"].replace("https://api.chess.com/pub/country/","")),
            if "location" in player.keys():
                location.append(player["location"])        
            else:
                location.append("")                
            last_online.append(player["last_online"])
            joined.append(player["joined"])
            status.append(player["status"])
            if "is_streamer" in player.keys():
                is_streamer.append(player["is_streamer"])                       
            else:     
                is_streamer.append("")
        except:
            print("unexpected error")

        i += 1 

    player_dict = {
        "player_id":player_id,
        "username":player_username,
        "title":title,
        "followers":followers,
        "country":country,
        "location":location,
        "last_online":last_online,
        "joined":joined,
        "status":status,
        "is_streamer":is_streamer
    }
    chessplayer_details_df = pd.DataFrame(player_dict)

    # chessplayer_df.to_csv(output_data_players, index=True,index_label="player_index") 
    
    return chessplayer_details_df

In [7]:
# api calls for each country in country_filepath
# generates csv file with list of usernames for each country output_data/players_{country_code}.csv
def get_usernames_country_api():
    country_df = pd.read_csv(country_filepath)
    country_df

    for index, row in country_df.iterrows():        
        try:          
            country_name = row["Country"]
            country_code = row["Code"]            
            output_file_country = f"output_data/players_{country_code}.csv"

            get_usernames_country(country_code,output_file_country)
            # time.sleep(1)  

        except: 
            print("unepxected error/skipping country")

```{
  "avatar": "https://images.chesscomfiles.com/uploads/v1/user/14775486.9072453d.200x200o.50bb2d10a7d5.jpeg",
  "player_id": 14775486,
  "@id": "https://api.chess.com/pub/player/140mariam",
  "url": "https://www.chess.com/member/140mariam",
  "name": "Mariam Avetisyan",
  "username": "140mariam",
  "title": "WFM",
  "followers": 56,
  "country": "https://api.chess.com/pub/country/AM",
  "last_online": 1609780423,
  "joined": 1385829847,
  "status": "premium",
  "is_streamer": false
}
```

In [8]:
# check if output_data_file exists already, if it doesn't exist, do api call to get username data
#if (path.exists(output_data_players)):
    # ****************
    # pull prevously generated and saved output data from csv
    #chessplayer_df = pd.read_csv(output_data_players)
#else:    
    # run api calls for each chess.com username
    # this step is skipped if the output_data_file already exists
    # !!!!! DELETE CSV OUTPUT FILE to generate new playerdata    
    #playerdata = get_playerdata_api(player_usernames)
    # gets list of titled players
    #playerslist_data = get_titledplayers_api(titled_players_type)
    
    
    

In [9]:
## Get sample of users from csv file of one country (CANADA)
def get_sample_player_details(country):
    # country = "CA"
    players_country_file = f"output_data/players_{country}.csv"

    chessplayers_country_df = pd.read_csv(players_country_file)
    
    # get username count from country df
    chessplayers_count = len(chessplayers_country_df)    
    
    # if population is less than 5000 use population, if >= 5000 use 5000 as sample size
    if (chessplayers_count < 5000):        
        sample_count = chessplayers_count    
    if (chessplayers_count >= 5000):
        sample_count = 5000
        
    print(f"{sample_count} is the sample size of {country} population ({chessplayers_count})\n")
    data = np.random.randint(0, chessplayers_count, size=sample_count)

    sample_country_usernames = []
    for index in data:    
        username = chessplayers_country_df.iloc[index]["username"]    
        sample_country_usernames.append(username)


    playerdata = get_playerdata_api(sample_country_usernames)
    
    return playerdata


In [9]:
# CANADA - get player details from CANADA usernames
playerdata_CA = get_sample_player_details("CA")
player_CA_df = get_player_dataframe(playerdata_CA)
output_data_players_CA = 'output_data/player_details_CA.csv'
player_CA_df.to_csv(output_data_players_CA, index=True,index_label="player_index") 

In [13]:
# RUSSIA - get player details from RUSSIA usernames
playerdata_RU = get_sample_player_details("RU")
player_RU_df = get_player_dataframe(playerdata_RU)
output_data_players_RU = 'output_data/player_details_RU.csv'
player_RU_df.to_csv(output_data_players_RU, index=True,index_label="player_index") 

5000 is the sample size of RU population (103656)

Index 0 fetching player data for player ivanpetr
Index 1 fetching player data for player hukycenok
Index 2 fetching player data for player rst0000
Index 3 fetching player data for player art_em_up
Index 4 fetching player data for player boltina
Index 5 fetching player data for player 89blues
Index 6 fetching player data for player afanasij1914
Index 7 fetching player data for player jessie108
Index 8 fetching player data for player asveider
Index 9 fetching player data for player zolrus16
Index 10 fetching player data for player shved1974
Index 11 fetching player data for player pobeditel_08
Index 12 fetching player data for player mihburkov
Index 13 fetching player data for player brov79
Index 14 fetching player data for player kachviktor
Index 15 fetching player data for player peaceful0warrior
Index 16 fetching player data for player juniorzebra
Index 17 fetching player data for player vkurchatkin
Index 18 fetching player data for p

Index 157 fetching player data for player protopop77
Index 158 fetching player data for player gr4xx
Index 159 fetching player data for player sash0milash
Index 160 fetching player data for player solari17
Index 161 fetching player data for player muromec13
Index 162 fetching player data for player olegb83
Index 163 fetching player data for player ametisty
Index 164 fetching player data for player mizzzzzzgun
Index 165 fetching player data for player komdizzle
Index 166 fetching player data for player deadly_donut
Index 167 fetching player data for player ratnikxyz
Index 168 fetching player data for player avg_protection
Index 169 fetching player data for player urigus
Index 170 fetching player data for player chessthenbless
Index 171 fetching player data for player laughingelk
Index 172 fetching player data for player andrewsharaev
Index 173 fetching player data for player yerand7
Index 174 fetching player data for player amyforeal2
Index 175 fetching player data for player andrey_chf

Index 313 fetching player data for player smile5598
Index 314 fetching player data for player xzadjen
Index 315 fetching player data for player niinada
Index 316 fetching player data for player venia74
Index 317 fetching player data for player eyerabbit
Index 318 fetching player data for player elis0086
Index 319 fetching player data for player serg400
Index 320 fetching player data for player alexandro1975
Index 321 fetching player data for player zanwtp
Index 322 fetching player data for player monahnestor
Index 323 fetching player data for player dabasov
Index 324 fetching player data for player vanyamasterninja
Index 325 fetching player data for player marivylegzhanina
Index 326 fetching player data for player sovloki
Index 327 fetching player data for player kirmodin
Index 328 fetching player data for player desperadodanil
Index 329 fetching player data for player alekseymar
Index 330 fetching player data for player sergeykoshev
Index 331 fetching player data for player ckyhc123
I

Index 470 fetching player data for player brutal_kolobok
Index 471 fetching player data for player monica893
Index 472 fetching player data for player valeeriyaa
Index 473 fetching player data for player egorka635
Index 474 fetching player data for player psinneraf
Index 475 fetching player data for player dm0705
Index 476 fetching player data for player zainulla
Index 477 fetching player data for player rudenokslava
Index 478 fetching player data for player k_mike
Index 479 fetching player data for player shingenn
Index 480 fetching player data for player midnoon
Index 481 fetching player data for player mirkin4
Index 482 fetching player data for player sharkness007
Index 483 fetching player data for player gary0081
Index 484 fetching player data for player alaltru
Index 485 fetching player data for player greshnov_ivan
Index 486 fetching player data for player efremova_vii
Index 487 fetching player data for player taykov
Index 488 fetching player data for player mctatarochka
Index 48

Index 626 fetching player data for player adeliya1822
Index 627 fetching player data for player lak1n
Index 628 fetching player data for player civilcase
Index 629 fetching player data for player vovamoroz
Index 630 fetching player data for player lapin_sergey
Index 631 fetching player data for player s_konem_naa8
Index 632 fetching player data for player stepanpotey-ipa
Index 633 fetching player data for player kirrees
Index 634 fetching player data for player arinakov
Index 635 fetching player data for player rei3772
Index 636 fetching player data for player georgyefanov
Index 637 fetching player data for player geymonster
Index 638 fetching player data for player coffee-zombie
Index 639 fetching player data for player dimadyrygin
Index 640 fetching player data for player valchess13
Index 641 fetching player data for player daniil-n
Index 642 fetching player data for player eclatmk
Index 643 fetching player data for player grossmeister2019
Index 644 fetching player data for player al

...

Index 4469 fetching player data for player meta_cube
Index 4470 fetching player data for player zzzzzzelten
Index 4471 fetching player data for player iigoruha
Index 4472 fetching player data for player chessclub_64
Index 4473 fetching player data for player masimilian
Index 4474 fetching player data for player dmitriyvdk
Index 4475 fetching player data for player vladimirsurov
Index 4476 fetching player data for player fosfor195
Index 4477 fetching player data for player sputer22
Index 4478 fetching player data for player 1802a
Index 4479 fetching player data for player spiffymarble
Index 4480 fetching player data for player yafizzzov
Index 4481 fetching player data for player mymateturn
Index 4482 fetching player data for player mikhailnaumov27
Index 4483 fetching player data for player alexxxan2610
Index 4484 fetching player data for player quiet_hour
Index 4485 fetching player data for player shomilinho
Index 4486 fetching player data for player greenliner
Index 4487 fetching playe

Index 4621 fetching player data for player trolliwally
Index 4622 fetching player data for player romanvlasoff
Index 4623 fetching player data for player amarei77
Index 4624 fetching player data for player sem1465
Index 4625 fetching player data for player roza0770
Index 4626 fetching player data for player kerij14
Index 4627 fetching player data for player vdergachoff
Index 4628 fetching player data for player haimkat
Index 4629 fetching player data for player mikhailmovchan
Index 4630 fetching player data for player dunga63
Index 4631 fetching player data for player chessmouse1
Index 4632 fetching player data for player winchester1388
Index 4633 fetching player data for player kirka377
Index 4634 fetching player data for player savvaloginov
Index 4635 fetching player data for player murphqw
Index 4636 fetching player data for player biatlonist10
Index 4637 fetching player data for player liquipups
Index 4638 fetching player data for player diannadilaila
Index 4639 fetching player dat

Index 4775 fetching player data for player chattybagpipe
Index 4776 fetching player data for player toria111
Index 4777 fetching player data for player cheesmaster777777
Index 4778 fetching player data for player artik353
Index 4779 fetching player data for player originalzipper
Index 4780 fetching player data for player netnet1048
Index 4781 fetching player data for player raccoon6e
Index 4782 fetching player data for player alimkozhenov
Index 4783 fetching player data for player deni5018
Index 4784 fetching player data for player vyurok
Index 4785 fetching player data for player serg1977786
Index 4786 fetching player data for player 414ok
Index 4787 fetching player data for player nastia565
Index 4788 fetching player data for player ckyhc123
Index 4789 fetching player data for player tired_tiger
Index 4790 fetching player data for player vaili
Index 4791 fetching player data for player milena1415
Index 4792 fetching player data for player ramzessecond
Index 4793 fetching player data 

Index 4927 fetching player data for player debuer77
Index 4928 fetching player data for player aram_tsamtsam
Index 4929 fetching player data for player valerii1976
Index 4930 fetching player data for player feliksburtyuk
Index 4931 fetching player data for player susemka
Index 4932 fetching player data for player lissinichkin
Index 4933 fetching player data for player smirnovs3000
Index 4934 fetching player data for player zverev49
Index 4935 fetching player data for player mmm235
Index 4936 fetching player data for player escobar38
Index 4937 fetching player data for player victor18041980
Index 4938 fetching player data for player valllery
Index 4939 fetching player data for player thunderdamn76
Index 4940 fetching player data for player kirillmed1985
Index 4941 fetching player data for player aliagalimova
Index 4942 fetching player data for player qw333
Index 4943 fetching player data for player i580
Index 4944 fetching player data for player maxwill90
Index 4945 fetching player data

Index 3421 processing username my126
Index 3422 processing username dug_o
Index 3423 processing username sergei-po-nastroeniu
Index 3424 processing username liarm
Index 3425 processing username 5bi4
Index 3426 processing username sablin_alexey
Index 3427 processing username yfa102102
Index 3428 processing username lada2703
Index 3429 processing username mczenit
Index 3430 processing username peterprigor
Index 3431 processing username ilyas_nix
Index 3432 processing username coolsurgion
Index 3433 processing username begemot8
Index 3434 processing username therealmast
Index 3435 processing username andrewsudarikov
Index 3436 processing username sasharulit1
Index 3437 processing username alinatret
Index 3438 processing username katsu_nyan
Index 3439 processing username dimkov2
Index 3440 processing username infud
Index 3441 processing username craxulty
Index 3442 processing username vegetut
Index 3443 processing username bonitoy
Index 3444 processing username vasiliyer
Index 3445 process

In [14]:
# MEXICO - get player details from MEXICO usernames
playerdata_MX = get_sample_player_details("MX")
player_MX_df = get_player_dataframe(playerdata_MX)
output_data_players_MX = 'output_data/player_details_MX.csv'
player_MX_df.to_csv(output_data_players_MX, index=True,index_label="player_index") 

5000 is the sample size of MX population (65853)

Index 0 fetching player data for player josuegch
Index 1 fetching player data for player pacopac1
Index 2 fetching player data for player kikequesos
Index 3 fetching player data for player rick_03
Index 4 fetching player data for player raulhernandezgarcia
Index 5 fetching player data for player penetreitor235
Index 6 fetching player data for player chnoriega
Index 7 fetching player data for player danielcdl
Index 8 fetching player data for player alemanias
Index 9 fetching player data for player j_rendon98
Index 10 fetching player data for player pablo1188
Index 11 fetching player data for player cvazquez48
Index 12 fetching player data for player chubo1376
Index 13 fetching player data for player deambulnte
Index 14 fetching player data for player llockdownl
Index 15 fetching player data for player reginamestre
Index 16 fetching player data for player warriorgod333
Index 17 fetching player data for player angelbaeza777
Index 18 fetchi

Index 156 fetching player data for player arlong-d
Index 157 fetching player data for player cocol81
Index 158 fetching player data for player yaz0808
Index 159 fetching player data for player salcedo13
Index 160 fetching player data for player hktr90
Index 161 fetching player data for player karis004
Index 162 fetching player data for player aramhub
Index 163 fetching player data for player babyjey69
Index 164 fetching player data for player ehrodgz
Index 165 fetching player data for player imiazu
Index 166 fetching player data for player archiame
Index 167 fetching player data for player cheeringpasture
Index 168 fetching player data for player rolos84
Index 169 fetching player data for player knigh604
Index 170 fetching player data for player rdavilac
Index 171 fetching player data for player duende7
Index 172 fetching player data for player romanzm
Index 173 fetching player data for player frodguz
Index 174 fetching player data for player cliffor1
Index 175 fetching player data for

Index 312 fetching player data for player monkeykingelian
Index 313 fetching player data for player carlos_palacios
Index 314 fetching player data for player jonathanantonio
Index 315 fetching player data for player servingardea
Index 316 fetching player data for player bruce5011
Index 317 fetching player data for player jefejime
Index 318 fetching player data for player nani2737
Index 319 fetching player data for player scroud_83
Index 320 fetching player data for player alucard1208z
Index 321 fetching player data for player peonch3ss
Index 322 fetching player data for player javiervallejo
Index 323 fetching player data for player davidsea27089
Index 324 fetching player data for player yayanman
Index 325 fetching player data for player itzy310
Index 326 fetching player data for player villegas72
Index 327 fetching player data for player fernandosaid7
Index 328 fetching player data for player argenta2k
Index 329 fetching player data for player horaceleon
Index 330 fetching player data 

Index 468 fetching player data for player medrano_2099
Index 469 fetching player data for player el_centinela
Index 470 fetching player data for player yorick_el_bufon
Index 471 fetching player data for player jonathancn16
Index 472 fetching player data for player julian_2
Index 473 fetching player data for player ortizkey
Index 474 fetching player data for player landarck
Index 475 fetching player data for player alucard245
Index 476 fetching player data for player katiarlen
Index 477 fetching player data for player veeadams12
Index 478 fetching player data for player angelgs94
Index 479 fetching player data for player jsehxl
Index 480 fetching player data for player spartanote
Index 481 fetching player data for player alansync
Index 482 fetching player data for player glm2020
Index 483 fetching player data for player zottacko
Index 484 fetching player data for player mauricio202
Index 485 fetching player data for player jara2811
Index 486 fetching player data for player nobodylikesri

Index 624 fetching player data for player tiradoo
Index 625 fetching player data for player ricardomich
Index 626 fetching player data for player franz0075
Index 627 fetching player data for player jemsego
Index 628 fetching player data for player beta7
Index 629 fetching player data for player kat1612
Index 630 fetching player data for player muchomejorquerana
Index 631 fetching player data for player ponchotorres
Index 632 fetching player data for player kylerapps
Index 633 fetching player data for player isaama51
Index 634 fetching player data for player telvannimage
Index 635 fetching player data for player nahumrebolledo
Index 636 fetching player data for player ramsesponce
Index 637 fetching player data for player elingeniebrio
Index 638 fetching player data for player daxmer
Index 639 fetching player data for player ariel5607
Index 640 fetching player data for player enrique1895
Index 641 fetching player data for player croacktable
Index 642 fetching player data for player cooki

...

Index 4456 fetching player data for player cristocalzada
Index 4457 fetching player data for player travis2359
Index 4458 fetching player data for player adolfo_night
Index 4459 fetching player data for player franciscobernal7
Index 4460 fetching player data for player fabricio10
Index 4461 fetching player data for player antua2
Index 4462 fetching player data for player juggernaut61
Index 4463 fetching player data for player ramiguel8
Index 4464 fetching player data for player morrinni
Index 4465 fetching player data for player rgonzalezvega1
Index 4466 fetching player data for player 1409mich
Index 4467 fetching player data for player chequeee
Index 4468 fetching player data for player safari66
Index 4469 fetching player data for player masantor
Index 4470 fetching player data for player capi1003
Index 4471 fetching player data for player jmreyesrugerio
Index 4472 fetching player data for player armandopaquini
Index 4473 fetching player data for player jabond27
Index 4474 fetching pl

Index 4610 fetching player data for player lunarooyoss
Index 4611 fetching player data for player johanbueno
Index 4612 fetching player data for player linko17
Index 4613 fetching player data for player alex6995
Index 4614 fetching player data for player diegoramrezd
Index 4615 fetching player data for player ivan3075
Index 4616 fetching player data for player cesmat367
Index 4617 fetching player data for player guillermo1504
Index 4618 fetching player data for player fabianmontano
Index 4619 fetching player data for player isaacmejia23
Index 4620 fetching player data for player kraknik
Index 4621 fetching player data for player rafarlezama
Index 4622 fetching player data for player abel_1618
Index 4623 fetching player data for player rafacs22
Index 4624 fetching player data for player wizhard2705
Index 4625 fetching player data for player elpuma1981
Index 4626 fetching player data for player roob16
Index 4627 fetching player data for player diego3174
Index 4628 fetching player data fo

Index 4763 fetching player data for player efrainameca
Index 4764 fetching player data for player alberthoffman11
Index 4765 fetching player data for player rolex2409
Index 4766 fetching player data for player luisruvalcabachavez
Index 4767 fetching player data for player emiliano7752
Index 4768 fetching player data for player gengis66
Index 4769 fetching player data for player superchessy2019
Index 4770 fetching player data for player themexicantarzan
Index 4771 fetching player data for player horaciooropeza
Index 4772 fetching player data for player mollejascastro
Index 4773 fetching player data for player oscarert02
Index 4774 fetching player data for player calderongx
Index 4775 fetching player data for player jalomojalomo97
Index 4776 fetching player data for player steeler1961
Index 4777 fetching player data for player ebaez12
Index 4778 fetching player data for player melquizedecm
Index 4779 fetching player data for player braku619
Index 4780 fetching player data for player osca

Index 4914 fetching player data for player eduardodom
Index 4915 fetching player data for player yvavc
Index 4916 fetching player data for player urielruano
Index 4917 fetching player data for player lunabonita
Index 4918 fetching player data for player vtec
Index 4919 fetching player data for player damislove
Index 4920 fetching player data for player sirpuckling
Index 4921 fetching player data for player everastorga
Index 4922 fetching player data for player satangalvan
Index 4923 fetching player data for player 3dher18
Index 4924 fetching player data for player alexiscasasquintanar
Index 4925 fetching player data for player feral662
Index 4926 fetching player data for player alfonsolopez2
Index 4927 fetching player data for player luis230602
Index 4928 fetching player data for player zars0
Index 4929 fetching player data for player cesa0279
Index 4930 fetching player data for player kenblox
Index 4931 fetching player data for player cmadachess
Index 4932 fetching player data for pla

Index 3355 processing username mesias2353
Index 3356 processing username yourdaddy42
Index 3357 processing username fanny7067
Index 3358 processing username sag2173
Index 3359 processing username hambertoy
Index 3360 processing username xavaaudelo
Index 3361 processing username xabovar
Index 3362 processing username milan2410
Index 3363 processing username diiannaxd
Index 3364 processing username s3b4st
Index 3365 processing username sani157
Index 3366 processing username enriqueadabache
Index 3367 processing username jorgeelcapi3240
Index 3368 processing username josuejs
Index 3369 processing username kaijuking07
Index 3370 processing username omarpaniagua
Index 3371 processing username loky78
Index 3372 processing username victor_de_leon
Index 3373 processing username angelruizm
Index 3374 processing username jesusmoya921
Index 3375 processing username eayonm
Index 3376 processing username agedcrane6
Index 3377 processing username ivandraggo23
Index 3378 processing username lrgckp
In

In [8]:
#IRELAND - get player details from IRELAND usernames
playerdata_IE = get_sample_player_details("IE")
player_IE_df = get_player_dataframe(playerdata_IE)
output_data_players_IE = 'output_data/player_details_IE.csv'
player_IE_df.to_csv(output_data_players_IE, index=True,index_label="player_index") 

5000 is the sample size of IE population (19961)

Index 0 fetching player data for player chesschess180
Index 1 fetching player data for player har79
Index 2 fetching player data for player jimbox10
Index 3 fetching player data for player kraze111
Index 4 fetching player data for player iitzdaltonxd
Index 5 fetching player data for player mcguire88
Index 6 fetching player data for player scoopy38
Index 7 fetching player data for player ciaranjmcc
Index 8 fetching player data for player kidcharlemagne94
Index 9 fetching player data for player very-average-player
Index 10 fetching player data for player shanery
Index 11 fetching player data for player bren_dan12
Index 12 fetching player data for player socialcrow
Index 13 fetching player data for player lorcanwalsh
Index 14 fetching player data for player davidokane
Index 15 fetching player data for player danny967
Index 16 fetching player data for player lottie035
Index 17 fetching player data for player oreen37
Index 18 fetching player

Index 157 fetching player data for player zannzu
Index 158 fetching player data for player markfp
Index 159 fetching player data for player dy1an77
Index 160 fetching player data for player wmcc89
Index 161 fetching player data for player no1chessplayerxx
Index 162 fetching player data for player pquinn232
Index 163 fetching player data for player cubysthebest
Index 164 fetching player data for player kerrie3
Index 165 fetching player data for player lahamilton14
Index 166 fetching player data for player fernan77fg
Index 167 fetching player data for player lfc2690
Index 168 fetching player data for player kledi_qarraj
Index 169 fetching player data for player piarasol
Index 170 fetching player data for player superkav83
Index 171 fetching player data for player margarinae
Index 172 fetching player data for player concorde24
Index 173 fetching player data for player duff611
Index 174 fetching player data for player queeniecorn
Index 175 fetching player data for player ulyesses
Index 176

Index 313 fetching player data for player anthonygt92
Index 314 fetching player data for player nocallaghan
Index 315 fetching player data for player wagonwheel
Index 316 fetching player data for player leroyownsstud
Index 317 fetching player data for player ribeena
Index 318 fetching player data for player melike949
Index 319 fetching player data for player jas1506
Index 320 fetching player data for player ciaranod
Index 321 fetching player data for player chamsmalams
Index 322 fetching player data for player xolegote
Index 323 fetching player data for player laoch19
Index 324 fetching player data for player kpeezy4
Index 325 fetching player data for player pastaloop
Index 326 fetching player data for player matthewf93
Index 327 fetching player data for player geroshock
Index 328 fetching player data for player caoimhe23
Index 329 fetching player data for player steveng787
Index 330 fetching player data for player cornfriend
Index 331 fetching player data for player jaaashhh
Index 332

Index 469 fetching player data for player killfilip
Index 470 fetching player data for player ceerawn
Index 471 fetching player data for player andrewsw7
Index 472 fetching player data for player robertomc
Index 473 fetching player data for player hydrocelica
Index 474 fetching player data for player adambalfe123
Index 475 fetching player data for player jophyjohn01
Index 476 fetching player data for player frankielyons
Index 477 fetching player data for player aarconman
Index 478 fetching player data for player pegleggreg12
Index 479 fetching player data for player chessmanone111
Index 480 fetching player data for player amycassidy
Index 481 fetching player data for player liamdoyle
Index 482 fetching player data for player maxkeat
Index 483 fetching player data for player conordonohue
Index 484 fetching player data for player vihaan_hodade
Index 485 fetching player data for player thewompfella
Index 486 fetching player data for player kmandem
Index 487 fetching player data for player

Index 625 fetching player data for player hltl3r
Index 626 fetching player data for player denverkelly6
Index 627 fetching player data for player philallen0
Index 628 fetching player data for player kevinsgambit
Index 629 fetching player data for player youaregoingdownphil
Index 630 fetching player data for player asimpleboi
Index 631 fetching player data for player iraland
Index 632 fetching player data for player gmcarlsen3
Index 633 fetching player data for player nizzynizz
Index 634 fetching player data for player vertz1997
Index 635 fetching player data for player brianmccomedy
Index 636 fetching player data for player sly-cian
Index 637 fetching player data for player fofo12
Index 638 fetching player data for player ronanocarroll
Index 639 fetching player data for player ct1234
Index 640 fetching player data for player bobbyfishdeepblue
Index 641 fetching player data for player idletime1001
Index 642 fetching player data for player cpenalobel
Index 643 fetching player data for pl

...

Index 4769 fetching player data for player littled86
Index 4770 fetching player data for player transit08999
Index 4771 fetching player data for player rubynathan
Index 4772 fetching player data for player ifyn6
Index 4773 fetching player data for player simmons00
Index 4774 fetching player data for player fmolleri
Index 4775 fetching player data for player robburke01
Index 4776 fetching player data for player law813
Index 4777 fetching player data for player spoonsprenderblast
Index 4778 fetching player data for player chipoac
Index 4779 fetching player data for player ekeat
Index 4780 fetching player data for player wheeier
Index 4781 fetching player data for player lefella
Index 4782 fetching player data for player gary1001
Index 4783 fetching player data for player patbreensarmy
Index 4784 fetching player data for player hrmb69
Index 4785 fetching player data for player jafro_king
Index 4786 fetching player data for player eagle130e
Index 4787 fetching player data for player gpmp
I

Index 4924 fetching player data for player franner23
Index 4925 fetching player data for player stinkyjim4
Index 4926 fetching player data for player hare284
Index 4927 fetching player data for player prince_abubu
Index 4928 fetching player data for player chinakop
Index 4929 fetching player data for player bojanpetrovic11
Index 4930 fetching player data for player eoin5s
Index 4931 fetching player data for player egan26
Index 4932 fetching player data for player glenrover
Index 4933 fetching player data for player niallliam1
Index 4934 fetching player data for player barkingdon
Index 4935 fetching player data for player roostgg
Index 4936 fetching player data for player xxxxchessmaster69xxx
Index 4937 fetching player data for player anndoyle
Index 4938 fetching player data for player stephenodriscoll
Index 4939 fetching player data for player imcolm
Index 4940 fetching player data for player theecholalia
Index 4941 fetching player data for player philipmac4
Index 4942 fetching player 

Index 1042 processing username ericcass16
Index 1043 processing username darragh424
Index 1044 processing username monsterdude65
Index 1045 processing username daisybrightt
Index 1046 processing username nel8001
Index 1047 processing username toog
Index 1048 processing username brenndann
Index 1049 processing username mayodog
Index 1050 processing username ollygould03
Index 1051 processing username cmsq123
Index 1052 processing username frankoconnor708
Index 1053 processing username sameoldshamo
Index 1054 processing username chessmonger42
Index 1055 processing username portmarnock14
Index 1056 processing username janer51
Index 1057 processing username fitzies
Index 1058 processing username fragileoink
Index 1059 processing username melay97
Index 1060 processing username drakula78
Index 1061 processing username fart_maniac
Index 1062 processing username djg648
Index 1063 processing username tonysoprano17
Index 1064 processing username darrylbrunton
Index 1065 processing username amarts

Index 3822 processing username polarpatch
Index 3823 processing username rraiin
Index 3824 processing username niamhherbert
Index 3825 processing username patch667
Index 3826 processing username frozenrawr
Index 3827 processing username cionnaith77
Index 3828 processing username superbrugha
Index 3829 processing username joshtothesmyth
Index 3830 processing username caroc22
Index 3831 processing username howsthehorsymove
Index 3832 processing username drmagicianmuckergoat
Index 3833 processing username gavinh8
Index 3834 processing username particle_soup
Index 3835 processing username cailin_ficheall
Index 3836 processing username bearpig35v2
Index 3837 processing username ezije
Index 3838 processing username joecorish
Index 3839 processing username jessibabyxo
Index 3840 processing username hitmann101
Index 3841 processing username kormak1234
Index 3842 processing username ivo-97
Index 3843 processing username pelasky
Index 3844 processing username secretpyromaniac
Index 3845 processi

Index 4635 processing username ninja_hand_face
Index 4636 processing username pk235
Index 4637 processing username senclarke
Index 4638 processing username edvardas123
Index 4639 processing username sabb0601
Index 4640 processing username birdnerd135
Index 4641 processing username jordangt
Index 4642 processing username bouchier59
Index 4643 processing username jtsheehan10
Index 4644 processing username wexfordboyo
Index 4645 processing username darragh424
Index 4646 processing username christopherstewart01
Index 4647 processing username paulspecter
Index 4648 processing username hunskelper1996
Index 4649 processing username jackkna
Index 4650 processing username fitcrayon234661
Index 4651 processing username kikz2
Index 4652 processing username killianod
Index 4653 processing username lee250
Index 4654 processing username 00nn72000
Index 4655 processing username pjlee167
Index 4656 processing username damodai
Index 4657 processing username olchikk
Index 4658 processing username cormac

In [9]:
#NEW ZEALAND - get player details from NEW ZEALAND usernames
playerdata_NZ = get_sample_player_details("NZ")
player_NZ_df = get_player_dataframe(playerdata_NZ)
output_data_players_NZ = 'output_data/player_details_NZ.csv'
player_NZ_df.to_csv(output_data_players_NZ, index=True,index_label="player_index") 

5000 is the sample size of NZ population (11659)

Index 0 fetching player data for player neil1691
Index 1 fetching player data for player hooolycow
Index 2 fetching player data for player pointblank2
Index 3 fetching player data for player bennie9
Index 4 fetching player data for player auto0
Index 5 fetching player data for player thesouthernsnake
Index 6 fetching player data for player cal107
Index 7 fetching player data for player alexanderwoolrych
Index 8 fetching player data for player crazyambz
Index 9 fetching player data for player devilwilliam
Index 10 fetching player data for player saurabhjs
Index 11 fetching player data for player philf1001
Index 12 fetching player data for player weta0
Index 13 fetching player data for player hypnotickitten
Index 14 fetching player data for player dangeruce
Index 15 fetching player data for player kiwibattler2020
Index 16 fetching player data for player bigrc90
Index 17 fetching player data for player lordrackleton
Index 18 fetching playe

Index 156 fetching player data for player najig
Index 157 fetching player data for player garthsidious
Index 158 fetching player data for player gillesp
Index 159 fetching player data for player roguegrogan
Index 160 fetching player data for player monkdavies
Index 161 fetching player data for player triskellios
Index 162 fetching player data for player ryan100123
Index 163 fetching player data for player braxtonphillips
Index 164 fetching player data for player wikiriwhi1
Index 165 fetching player data for player arfzarfz
Index 166 fetching player data for player the_kid_nz
Index 167 fetching player data for player sackydacky
Index 168 fetching player data for player smokeyrob
Index 169 fetching player data for player poodlepig
Index 170 fetching player data for player angelseb123
Index 171 fetching player data for player cheeseroll9
Index 172 fetching player data for player madeearlier
Index 173 fetching player data for player joethelegend1
Index 174 fetching player data for player r

Index 312 fetching player data for player roobydoobydoo
Index 313 fetching player data for player thatskinnydude
Index 314 fetching player data for player godlymip
Index 315 fetching player data for player khalildean
Index 316 fetching player data for player etn_nz
Index 317 fetching player data for player unknownfound
Index 318 fetching player data for player julianw85
Index 319 fetching player data for player karnepaparoa
Index 320 fetching player data for player rev85
Index 321 fetching player data for player urmumsmumsmum
Index 322 fetching player data for player -_chess_-
Index 323 fetching player data for player brisketoon
Index 324 fetching player data for player dustyfrog1
Index 325 fetching player data for player hjimmy505
Index 326 fetching player data for player bestfriendslush
Index 327 fetching player data for player yam420
Index 328 fetching player data for player mystic_yodaa
Index 329 fetching player data for player alexreed11
Index 330 fetching player data for player i

Index 468 fetching player data for player yoshimitsu19
Index 469 fetching player data for player umangoes
Index 470 fetching player data for player eggybach
Index 471 fetching player data for player loudiris
Index 472 fetching player data for player rubrows92
Index 473 fetching player data for player theboakey
Index 474 fetching player data for player iriee
Index 475 fetching player data for player vassadc
Index 476 fetching player data for player jacquesellis
Index 477 fetching player data for player nathanrosechess
Index 478 fetching player data for player mcfuggles
Index 479 fetching player data for player g_b4102
Index 480 fetching player data for player willze
Index 481 fetching player data for player stuartdebute
Index 482 fetching player data for player andriy1999
Index 483 fetching player data for player sumedhamuk
Index 484 fetching player data for player fischer38
Index 485 fetching player data for player alkamist11
Index 486 fetching player data for player jackals012
Index 4

Index 625 fetching player data for player beastfrie
Index 626 fetching player data for player kiwibacon
Index 627 fetching player data for player nidhin
Index 628 fetching player data for player nimzo55
Index 629 fetching player data for player preston021
Index 630 fetching player data for player jetstreamxr
Index 631 fetching player data for player leafbox
Index 632 fetching player data for player dodgee
Index 633 fetching player data for player jordaneliu
Index 634 fetching player data for player supargillu
Index 635 fetching player data for player angryplayr
Index 636 fetching player data for player penneygirl
Index 637 fetching player data for player tsunamoo
Index 638 fetching player data for player king_tbang
Index 639 fetching player data for player arimm14
Index 640 fetching player data for player petethepossumman
Index 641 fetching player data for player battlekelpie
Index 642 fetching player data for player alp_pachino
Index 643 fetching player data for player vigtigper
Index

...

Index 4456 fetching player data for player curry_slayer1
Index 4457 fetching player data for player jd03601
Index 4458 fetching player data for player hemi-layer
Index 4459 fetching player data for player gmchilcanito
Index 4460 fetching player data for player ob1kxb
Index 4461 fetching player data for player 123wangking123
Index 4462 fetching player data for player m1020705
Index 4463 fetching player data for player fatblackaxe
Index 4464 fetching player data for player josh076
Index 4465 fetching player data for player loopymate
Index 4466 fetching player data for player crustychips
Index 4467 fetching player data for player needagoodgame
Index 4468 fetching player data for player lukamelchior
Index 4469 fetching player data for player alexcando
Index 4470 fetching player data for player kanawatoro
Index 4471 fetching player data for player mothergoose61
Index 4472 fetching player data for player gam232323
Index 4473 fetching player data for player dustynomad07
Index 4474 fetching pl

Index 4607 fetching player data for player cabbagevon
Index 4608 fetching player data for player catherine014
Index 4609 fetching player data for player spike_m
Index 4610 fetching player data for player ndosanjh
Index 4611 fetching player data for player methodman336
Index 4612 fetching player data for player gbkiwi
Index 4613 fetching player data for player kybnz
Index 4614 fetching player data for player ruiha
Index 4615 fetching player data for player richyrich220
Index 4616 fetching player data for player forestf255
Index 4617 fetching player data for player altichess
Index 4618 fetching player data for player chessongzx
Index 4619 fetching player data for player youdonemessedup
Index 4620 fetching player data for player cardrooo
Index 4621 fetching player data for player merlinthefisherman
Index 4622 fetching player data for player magnifica101
Index 4623 fetching player data for player hobbes_md
Index 4624 fetching player data for player giddytype
Index 4625 fetching player data

Index 4760 fetching player data for player zysygy5
Index 4761 fetching player data for player poptarthunter
Index 4762 fetching player data for player lordgrayson2000
Index 4763 fetching player data for player massmachinegun
Index 4764 fetching player data for player tsha716
Index 4765 fetching player data for player i_think_therefore_gm
Index 4766 fetching player data for player sabbysingh94
Index 4767 fetching player data for player emilywilson8318
Index 4768 fetching player data for player babyyodaluvu
Index 4769 fetching player data for player jbacb
Index 4770 fetching player data for player prawn30
Index 4771 fetching player data for player chessgobruh
Index 4772 fetching player data for player bigbluesulley
Index 4773 fetching player data for player tlite84
Index 4774 fetching player data for player imperial_knights
Index 4775 fetching player data for player learningtogm
Index 4776 fetching player data for player pandaa9131
Index 4777 fetching player data for player chadford64
In

Index 4912 fetching player data for player eoghanok
Index 4913 fetching player data for player bagofhelium
Index 4914 fetching player data for player nootnootmachine
Index 4915 fetching player data for player shaneo1236
Index 4916 fetching player data for player emosewag
Index 4917 fetching player data for player legslouth
Index 4918 fetching player data for player a-z-a-r
Index 4919 fetching player data for player lunarlo
Index 4920 fetching player data for player yungnutz
Index 4921 fetching player data for player cybeny
Index 4922 fetching player data for player alexanderbevin
Index 4923 fetching player data for player julznathan
Index 4924 fetching player data for player etheruim
Index 4925 fetching player data for player samarcher1
Index 4926 fetching player data for player bewegungsunfahig
Index 4927 fetching player data for player kawinduel
Index 4928 fetching player data for player calebjtaylor72
Index 4929 fetching player data for player bxnterr
Index 4930 fetching player data

Index 2830 processing username morpixnz
Index 2831 processing username sutty_87
Index 2832 processing username chris-dsilva
Index 2833 processing username simeon30
Index 2834 processing username wippa
Index 2835 processing username bcfjellerino
Index 2836 processing username pushbutton_auto
Index 2837 processing username persausion
Index 2838 processing username usernamehssjsjsj
Index 2839 processing username mapmarcel
Index 2840 processing username desainz
Index 2841 processing username taperz123
Index 2842 processing username sklerm
Index 2843 processing username tommyt21
Index 2844 processing username topbunk365
Index 2845 processing username smallcrook
Index 2846 processing username beachnik
Index 2847 processing username lionnz
Index 2848 processing username adam5081
Index 2849 processing username jameslbrown001
Index 2850 processing username samkiryakos
Index 2851 processing username bevisjiang
Index 2852 processing username stephenh-nz
Index 2853 processing username itnotoktobes

In [8]:
#NORWAY - get player details from NORWAY usernames 
playerdata_NO = get_sample_player_details("NO")
player_NO_df = get_player_dataframe(playerdata_NO)
output_data_players_NO = 'output_data/player_details_NO.csv'
player_NO_df.to_csv(output_data_players_NO, index=True, index_label="player_index")


5000 is the sample size of NO population (43165)

Index 0 fetching player data for player checkumate88
Index 1 fetching player data for player uvalhal
Index 2 fetching player data for player bernten0284
Index 3 fetching player data for player henaar
Index 4 fetching player data for player toralida
Index 5 fetching player data for player momyrland
Index 6 fetching player data for player rag80
Index 7 fetching player data for player pukern
Index 8 fetching player data for player eirik77
Index 9 fetching player data for player einarht
Index 10 fetching player data for player kronkel58
Index 11 fetching player data for player kiwibob3
Index 12 fetching player data for player cetus65
Index 13 fetching player data for player rekekasparov
Index 14 fetching player data for player jaybello
Index 15 fetching player data for player artsoo
Index 16 fetching player data for player rogereiterjord
Index 17 fetching player data for player didrikbockmann
Index 18 fetching player data for player sostu
I

Index 160 fetching player data for player ferje
Index 161 fetching player data for player superpoelsa
Index 162 fetching player data for player lyngis90
Index 163 fetching player data for player superknott
Index 164 fetching player data for player evenero2
Index 165 fetching player data for player dylan54
Index 166 fetching player data for player songoten
Index 167 fetching player data for player jonuno1
Index 168 fetching player data for player mester2
Index 169 fetching player data for player flemmingsteffensen
Index 170 fetching player data for player canoy94
Index 171 fetching player data for player onesbakk
Index 172 fetching player data for player andrerut
Index 173 fetching player data for player torgeirlr
Index 174 fetching player data for player harila1g
Index 175 fetching player data for player jenswannebo
Index 176 fetching player data for player wadumene
Index 177 fetching player data for player hakon95
Index 178 fetching player data for player iamkc
Index 179 fetching play

Index 320 fetching player data for player darkknightmatt
Index 321 fetching player data for player cato_thordendal
Index 322 fetching player data for player oedegarden
Index 323 fetching player data for player lfberge
Index 324 fetching player data for player roffe01
Index 325 fetching player data for player pildenpene
Index 326 fetching player data for player gaaen
Index 327 fetching player data for player aksel2108
Index 328 fetching player data for player julkul
Index 329 fetching player data for player odinlyngset
Index 330 fetching player data for player rune1988
Index 331 fetching player data for player nash3
Index 332 fetching player data for player giggsen
Index 333 fetching player data for player odini420
Index 334 fetching player data for player dizlogic
Index 335 fetching player data for player oyvindmold
Index 336 fetching player data for player david_sand
Index 337 fetching player data for player thybotwin
Index 338 fetching player data for player yonas803
Index 339 fetchi

Index 478 fetching player data for player jorkol
Index 479 fetching player data for player iamjome
Index 480 fetching player data for player mcfarland72
Index 481 fetching player data for player djdan30
Index 482 fetching player data for player lektrosvendsen
Index 483 fetching player data for player swift11
Index 484 fetching player data for player bastigardi
Index 485 fetching player data for player mongosaurus
Index 486 fetching player data for player geirynwa
Index 487 fetching player data for player kriskindberg
Index 488 fetching player data for player loic-remis
Index 489 fetching player data for player heidien
Index 490 fetching player data for player jostein1904
Index 491 fetching player data for player karlalveng
Index 492 fetching player data for player ingunnmer
Index 493 fetching player data for player merkelig2
Index 494 fetching player data for player andreasvuo
Index 495 fetching player data for player zpar
Index 496 fetching player data for player giantamazon
Index 497

Index 637 fetching player data for player olasopp
Index 638 fetching player data for player eskilsundar
Index 639 fetching player data for player miniman2007
Index 640 fetching player data for player ainnstrand
Index 641 fetching player data for player terrasse
Index 642 fetching player data for player wolfsegg1968
Index 643 fetching player data for player yonas803
Index 644 fetching player data for player malmvegen
Index 645 fetching player data for player icewollowcum
Index 646 fetching player data for player chessandbach
Index 647 fetching player data for player thalllaaaaa
Index 648 fetching player data for player eventyra
Index 649 fetching player data for player odilos
Index 650 fetching player data for player toboss2007
Index 651 fetching player data for player cashmuni
Index 652 fetching player data for player triopews
Index 653 fetching player data for player toffi123
Index 654 fetching player data for player lestersquare
Index 655 fetching player data for player joelgn1
Index

...

Index 4519 fetching player data for player sondre420
Index 4520 fetching player data for player daanii
Index 4521 fetching player data for player aronaune09
Index 4522 fetching player data for player peremann1
Index 4523 fetching player data for player rolf1908
Index 4524 fetching player data for player aslefurevik
Index 4525 fetching player data for player cameco
Index 4526 fetching player data for player abdisongs
Index 4527 fetching player data for player tjabba01
Index 4528 fetching player data for player miasolh
Index 4529 fetching player data for player ceciliekj
Index 4530 fetching player data for player kongknut
Index 4531 fetching player data for player guldahl
Index 4532 fetching player data for player terjehammer
Index 4533 fetching player data for player grizlly1971
Index 4534 fetching player data for player zeaursamir
Index 4535 fetching player data for player boygunpowder
Index 4536 fetching player data for player hammerslag
Index 4537 fetching player data for player jozz

Index 4673 fetching player data for player mosse1978
Index 4674 fetching player data for player thekarlsen
Index 4675 fetching player data for player darknessenkrad
Index 4676 fetching player data for player lequeen
Index 4677 fetching player data for player voldermorten
Index 4678 fetching player data for player hallvard91
Index 4679 fetching player data for player thechineserestaurant
Index 4680 fetching player data for player emblaaurmo
Index 4681 fetching player data for player knutsverre
Index 4682 fetching player data for player romevalley
Index 4683 fetching player data for player peravaag
Index 4684 fetching player data for player pandapixels
Index 4685 fetching player data for player adrian98213
Index 4686 fetching player data for player potetbond1
Index 4687 fetching player data for player ultrazuz
Index 4688 fetching player data for player thnord
Index 4689 fetching player data for player youngseoiris
Index 4690 fetching player data for player thegolfboy08
Index 4691 fetchin

Index 4828 fetching player data for player goran2002
Index 4829 fetching player data for player lzstyles
Index 4830 fetching player data for player dannygundersen
Index 4831 fetching player data for player ownedfail13
Index 4832 fetching player data for player pnaps3
Index 4833 fetching player data for player mar10ngut1
Index 4834 fetching player data for player crazygulost
Index 4835 fetching player data for player lordmunk
Index 4836 fetching player data for player snfall
Index 4837 fetching player data for player rabbestappe
Index 4838 fetching player data for player marirol
Index 4839 fetching player data for player danastana8
Index 4840 fetching player data for player discodverg
Index 4841 fetching player data for player glossly
Index 4842 fetching player data for player martiniusolini
Index 4843 fetching player data for player fyrst1
Index 4844 fetching player data for player joethesmo
Index 4845 fetching player data for player edelin75
Index 4846 fetching player data for player 

Index 4983 fetching player data for player ibrafit
Index 4984 fetching player data for player okvalur
Index 4985 fetching player data for player edvard1931
Index 4986 fetching player data for player bakerlook
Index 4987 fetching player data for player alfno
Index 4988 fetching player data for player happi73
Index 4989 fetching player data for player steinarsimensen
Index 4990 fetching player data for player piboe
Index 4991 fetching player data for player solo10111
Index 4992 fetching player data for player olaierkul
Index 4993 fetching player data for player nottekraka
Index 4994 fetching player data for player asterix_knut
Index 4995 fetching player data for player galacticspacewizard
Index 4996 fetching player data for player steele70
Index 4997 fetching player data for player sjakkspiller37
Index 4998 fetching player data for player fjeldfanten
Index 4999 fetching player data for player julvog
Index 0 processing username checkumate88
Index 1 processing username uvalhal
Index 2 proc

Index 2186 processing username salvelinus78
Index 2187 processing username kksl
Index 2188 processing username lupoli2
Index 2189 processing username bennaboss
Index 2190 processing username carlxn
Index 2191 processing username eimund5577
Index 2192 processing username nobelplayer
Index 2193 processing username mollekake
Index 2194 processing username treeag
Index 2195 processing username eriks1980
Index 2196 processing username torkst
Index 2197 processing username drunkistein
Index 2198 processing username ossan-bauer
Index 2199 processing username proximacentauri99
Index 2200 processing username tjulriksen
Index 2201 processing username terjehj
Index 2202 processing username lot1393
Index 2203 processing username gjeddekjella
Index 2204 processing username fariznadirrzayev
Index 2205 processing username torejs
Index 2206 processing username theviklink
Index 2207 processing username ewelo
Index 2208 processing username dritlegende
Index 2209 processing username krok45
Index 2210 pro

In [9]:
#SPAIN - get player details from SPAIN usernames 
playerdata_ES = get_sample_player_details("ES")
player_ES_df = get_player_dataframe(playerdata_ES)
output_data_players_ES = 'output_data/player_details_ES.csv'
player_ES_df.to_csv(output_data_players_ES, index=True, index_label="player_index")


5000 is the sample size of ES population (112180)

Index 0 fetching player data for player francescteixi
Index 1 fetching player data for player patrom
Index 2 fetching player data for player cristianreyna
Index 3 fetching player data for player tamaduste
Index 4 fetching player data for player chandelier1089
Index 5 fetching player data for player diegoalvarezb
Index 6 fetching player data for player davimatis
Index 7 fetching player data for player marche5
Index 8 fetching player data for player ivanpv_4
Index 9 fetching player data for player bolicubo
Index 10 fetching player data for player dock123
Index 11 fetching player data for player sanzarov2
Index 12 fetching player data for player miguel-moreau
Index 13 fetching player data for player omayma_346
Index 14 fetching player data for player ikeralfonso
Index 15 fetching player data for player valencianos2
Index 16 fetching player data for player adrimv96
Index 17 fetching player data for player ricardfont
Index 18 fetching playe

Index 158 fetching player data for player ari_meow
Index 159 fetching player data for player amvzz
Index 160 fetching player data for player zzoltg
Index 161 fetching player data for player joltra55
Index 162 fetching player data for player lixusdcm
Index 163 fetching player data for player unlimitedwifi
Index 164 fetching player data for player morguits
Index 165 fetching player data for player lusogm
Index 166 fetching player data for player zaragocita
Index 167 fetching player data for player feloms
Index 168 fetching player data for player doctorguta
Index 169 fetching player data for player arturito2034
Index 170 fetching player data for player santiabascal178
Index 171 fetching player data for player sarialex1
Index 172 fetching player data for player leoasparov
Index 173 fetching player data for player misterermo
Index 174 fetching player data for player geri331
Index 175 fetching player data for player mvisions
Index 176 fetching player data for player javiervazquez71
Index 177

Index 315 fetching player data for player drvsteinf
Index 316 fetching player data for player jowel12
Index 317 fetching player data for player adrianabarrosol
Index 318 fetching player data for player huguello
Index 319 fetching player data for player luisitopvg
Index 320 fetching player data for player carloscabeiro
Index 321 fetching player data for player shakkarf
Index 322 fetching player data for player tomsagu
Index 323 fetching player data for player manusanchis
Index 324 fetching player data for player sfl3cha
Index 325 fetching player data for player cancunov
Index 326 fetching player data for player solrac3223
Index 327 fetching player data for player marcocucchi1998
Index 328 fetching player data for player joseviputoamo
Index 329 fetching player data for player bajatepabajo
Index 330 fetching player data for player adolfobraa
Index 331 fetching player data for player ruben_rmn
Index 332 fetching player data for player megino20
Index 333 fetching player data for player rafa

Index 473 fetching player data for player purpelhust
Index 474 fetching player data for player victorbueu
Index 475 fetching player data for player gabrielcar
Index 476 fetching player data for player morcillosanz
Index 477 fetching player data for player fhrann
Index 478 fetching player data for player martals04
Index 479 fetching player data for player rocioab
Index 480 fetching player data for player olivandavid
Index 481 fetching player data for player zhule68
Index 482 fetching player data for player madmac56
Index 483 fetching player data for player marccarbo
Index 484 fetching player data for player angelbenito
Index 485 fetching player data for player nacho_dc
Index 486 fetching player data for player tetye
Index 487 fetching player data for player txominibanez
Index 488 fetching player data for player persefoine
Index 489 fetching player data for player roisa
Index 490 fetching player data for player mikejr08
Index 491 fetching player data for player cavalieratq
Index 492 fetc

Index 629 fetching player data for player fjgg79
Index 630 fetching player data for player manujglez
Index 631 fetching player data for player martiinn188
Index 632 fetching player data for player alvarake
Index 633 fetching player data for player currito7
Index 634 fetching player data for player wil9090
Index 635 fetching player data for player alvaroaira
Index 636 fetching player data for player lanurea
Index 637 fetching player data for player chino46
Index 638 fetching player data for player gmcris1
Index 639 fetching player data for player moisesjugon
Index 640 fetching player data for player juanjemohedano
Index 641 fetching player data for player kedeke93
Index 642 fetching player data for player erickiller83
Index 643 fetching player data for player norunil
Index 644 fetching player data for player inesillasastre
Index 645 fetching player data for player pedritochupete
Index 646 fetching player data for player manuelmn2021
Index 647 fetching player data for player magicsebs
In

...

Index 4482 fetching player data for player simasa17
Index 4483 fetching player data for player elogt
Index 4484 fetching player data for player jorgedandres
Index 4485 fetching player data for player mkwn
Index 4486 fetching player data for player lvav34
Index 4487 fetching player data for player illodejamejugar
Index 4488 fetching player data for player mazinguer1970
Index 4489 fetching player data for player crazyhutter_019
Index 4490 fetching player data for player marcbotil
Index 4491 fetching player data for player miguelix40
Index 4492 fetching player data for player plamen9
Index 4493 fetching player data for player rango92
Index 4494 fetching player data for player aleloules
Index 4495 fetching player data for player lorenfito74
Index 4496 fetching player data for player nastes76
Index 4497 fetching player data for player carmonadeecija
Index 4498 fetching player data for player enriquearazuri
Index 4499 fetching player data for player afonsoac
Index 4500 fetching player data f

Index 4637 fetching player data for player bielreco
Index 4638 fetching player data for player deivisfc10
Index 4639 fetching player data for player tiburcio66
Index 4640 fetching player data for player sangui
Index 4641 fetching player data for player nataliahrn
Index 4642 fetching player data for player culuta
Index 4643 fetching player data for player gm_hache
Index 4644 fetching player data for player talitronic
Index 4645 fetching player data for player uri-c
Index 4646 fetching player data for player josss58
Index 4647 fetching player data for player marioajedrez
Index 4648 fetching player data for player xaddry
Index 4649 fetching player data for player acou
Index 4650 fetching player data for player amfr19157
Index 4651 fetching player data for player luna588
Index 4652 fetching player data for player adolader
Index 4653 fetching player data for player pacitrio65
Index 4654 fetching player data for player jorhev2
Index 4655 fetching player data for player alddos
Index 4656 fetc

Index 4791 fetching player data for player cdecozar
Index 4792 fetching player data for player cantoriopolis
Index 4793 fetching player data for player perecr
Index 4794 fetching player data for player arielkeren
Index 4795 fetching player data for player tena23
Index 4796 fetching player data for player rond009
Index 4797 fetching player data for player traurco
Index 4798 fetching player data for player francisco_perez
Index 4799 fetching player data for player ohlala1969
Index 4800 fetching player data for player fdezalba
Index 4801 fetching player data for player jvalldom
Index 4802 fetching player data for player loreniius
Index 4803 fetching player data for player koldobi
Index 4804 fetching player data for player monigidibi
Index 4805 fetching player data for player laluchitevacila
Index 4806 fetching player data for player logicko
Index 4807 fetching player data for player unico7
Index 4808 fetching player data for player guillemfontllacay
Index 4809 fetching player data for pla

Index 4943 fetching player data for player genijiye
Index 4944 fetching player data for player franxu1988
Index 4945 fetching player data for player borja_kappa
Index 4946 fetching player data for player gargimm
Index 4947 fetching player data for player averiguados
Index 4948 fetching player data for player sbcolo
Index 4949 fetching player data for player liam-costello
Index 4950 fetching player data for player thestark04
Index 4951 fetching player data for player mvazquezgordillo
Index 4952 fetching player data for player chachis_50
Index 4953 fetching player data for player ar3tri3048
Index 4954 fetching player data for player al3x_07
Index 4955 fetching player data for player hilbertklein
Index 4956 fetching player data for player sertuso
Index 4957 fetching player data for player ivanduda17
Index 4958 fetching player data for player carloslebronjames
Index 4959 fetching player data for player rsbm1
Index 4960 fetching player data for player gerri_sarto13
Index 4961 fetching playe

Index 1412 processing username quiquelopez
Index 1413 processing username manolillo91
Index 1414 processing username adrianhuxley
Index 1415 processing username maruwat
Index 1416 processing username sheck92
Index 1417 processing username snnake
Index 1418 processing username vict2934
Index 1419 processing username vladmiedos
Index 1420 processing username luisospas
Index 1421 processing username ivanchu26
Index 1422 processing username danielcaro9
Index 1423 processing username estrogoff
Index 1424 processing username tmcrawler
Index 1425 processing username laplazoletadevalme
Index 1426 processing username 12pat21
Index 1427 processing username l888x
Index 1428 processing username raulito272
Index 1429 processing username alanblackk
Index 1430 processing username paco_90
Index 1431 processing username guitarricadelaisla
Index 1432 processing username jon1714
Index 1433 processing username agrau
Index 1434 processing username cramber13
Index 1435 processing username nileche
Index 1436

In [9]:
#BRAZIL - get player details from BRAZIL usernames 
playerdata_BR = get_sample_player_details("BR")
player_BR_df = get_player_dataframe(playerdata_BR)
output_data_players_BR = 'output_data/player_details_BR.csv'
player_BR_df.to_csv(output_data_players_BR, index=True, index_label="player_index")


5000 is the sample size of BR population (147040)

Index 0 fetching player data for player wellingtonsilveira
Index 1 fetching player data for player acrenan
Index 2 fetching player data for player glhaag
Index 3 fetching player data for player gorfoloko
Index 4 fetching player data for player juliopinheiro
Index 5 fetching player data for player wiliansp87
Index 6 fetching player data for player georgemarins
Index 7 fetching player data for player ygorelias
Index 8 fetching player data for player rss_free
Index 9 fetching player data for player sanches2609
Index 10 fetching player data for player srneuer
Index 11 fetching player data for player necromancergyn
Index 12 fetching player data for player gtdelas
Index 13 fetching player data for player anserkrey
Index 14 fetching player data for player hnrqmtts
Index 15 fetching player data for player brunaodojet
Index 16 fetching player data for player moreira743
Index 17 fetching player data for player tratortrator
Index 18 fetching play

Index 156 fetching player data for player ameliepoulaintt
Index 157 fetching player data for player luizbraz1946
Index 158 fetching player data for player tbarsotti
Index 159 fetching player data for player fabianoferrari
Index 160 fetching player data for player imazzocco
Index 161 fetching player data for player hugoprudente
Index 162 fetching player data for player williambessa22
Index 163 fetching player data for player arthur801
Index 164 fetching player data for player ricardomouramarques
Index 165 fetching player data for player malukinhow
Index 166 fetching player data for player lukhs33312
Index 167 fetching player data for player carlos5919
Index 168 fetching player data for player zeintsu
Index 169 fetching player data for player jesse800
Index 170 fetching player data for player mguelber
Index 171 fetching player data for player wolfgang352
Index 172 fetching player data for player lierner
Index 173 fetching player data for player ahchaves
Index 174 fetching player data for

Index 310 fetching player data for player heitorbelo2019
Index 311 fetching player data for player pedroyuri99
Index 312 fetching player data for player brenomir
Index 313 fetching player data for player lokodetoddynho
Index 314 fetching player data for player matheusaraujobranco
Index 315 fetching player data for player danielgimenes
Index 316 fetching player data for player tvictoracio
Index 317 fetching player data for player pilaochess
Index 318 fetching player data for player jerryamorim
Index 319 fetching player data for player maurinovisk
Index 320 fetching player data for player shinee10
Index 321 fetching player data for player ruivoviking
Index 322 fetching player data for player kaspaloves
Index 323 fetching player data for player ecs_u2
Index 324 fetching player data for player fernlsp
Index 325 fetching player data for player davidson123checkmate
Index 326 fetching player data for player jpvmendes
Index 327 fetching player data for player helizerobot
Index 328 fetching pla

Index 465 fetching player data for player ramon025
Index 466 fetching player data for player vic226
Index 467 fetching player data for player gcastroid
Index 468 fetching player data for player luck67
Index 469 fetching player data for player rafaelboschi
Index 470 fetching player data for player sefudeuperdeu10x
Index 471 fetching player data for player erikselbmann
Index 472 fetching player data for player elohimelshaday
Index 473 fetching player data for player edu308
Index 474 fetching player data for player yamir221
Index 475 fetching player data for player irinagmaia
Index 476 fetching player data for player new99
Index 477 fetching player data for player 09364524713
Index 478 fetching player data for player italoreis
Index 479 fetching player data for player nanoinxs
Index 480 fetching player data for player kawansilva
Index 481 fetching player data for player leoespanhol
Index 482 fetching player data for player ebraccialli
Index 483 fetching player data for player felipe1977
I

Index 621 fetching player data for player jsouza13
Index 622 fetching player data for player sen112
Index 623 fetching player data for player saiony
Index 624 fetching player data for player edilsonbraz
Index 625 fetching player data for player drisonn
Index 626 fetching player data for player venatordux
Index 627 fetching player data for player sagaz3
Index 628 fetching player data for player gequionschulz
Index 629 fetching player data for player henriqueandion
Index 630 fetching player data for player gustavo3840a
Index 631 fetching player data for player pedrodacosta89
Index 632 fetching player data for player henriquesantoantonio
Index 633 fetching player data for player calango84
Index 634 fetching player data for player sxgz
Index 635 fetching player data for player kayoponath
Index 636 fetching player data for player schmiito
Index 637 fetching player data for player rossinyavp
Index 638 fetching player data for player mcoradini
Index 639 fetching player data for player jprcost

...

Index 4740 fetching player data for player bielzera0
Index 4741 fetching player data for player aspiringink
Index 4742 fetching player data for player bernardo_chess
Index 4743 fetching player data for player cloud254
Index 4744 fetching player data for player vinibiazus
Index 4745 fetching player data for player batatinhagame12
Index 4746 fetching player data for player igorolb
Index 4747 fetching player data for player narigadao
Index 4748 fetching player data for player vicbastos
Index 4749 fetching player data for player michelkc
Index 4750 fetching player data for player miauzin
Index 4751 fetching player data for player ramoeltop
Index 4752 fetching player data for player reddish66
Index 4753 fetching player data for player freudthedroid
Index 4754 fetching player data for player pedrocharney
Index 4755 fetching player data for player andre_souza
Index 4756 fetching player data for player odescobridor
Index 4757 fetching player data for player tcost89
Index 4758 fetching player d

Index 4891 fetching player data for player cxrujv
Index 4892 fetching player data for player leonardoterrasilva1
Index 4893 fetching player data for player guihchaz45
Index 4894 fetching player data for player cfreitas
Index 4895 fetching player data for player viace
Index 4896 fetching player data for player rodrigowerty
Index 4897 fetching player data for player dimitrigringenkov
Index 4898 fetching player data for player rafael342
Index 4899 fetching player data for player weberlara
Index 4900 fetching player data for player josh_miller
Index 4901 fetching player data for player jacksonbom
Index 4902 fetching player data for player batistao
Index 4903 fetching player data for player john21xj6
Index 4904 fetching player data for player muffinw
Index 4905 fetching player data for player g92abriel
Index 4906 fetching player data for player esth81
Index 4907 fetching player data for player pinguim33
Index 4908 fetching player data for player bielchess69
Index 4909 fetching player data f

Index 635 processing username kayoponath
Index 636 processing username schmiito
Index 637 processing username rossinyavp
Index 638 processing username mcoradini
Index 639 processing username jprcosta
Index 640 processing username alinelb
Index 641 processing username adjuninho96
Index 642 processing username elefante5
Index 643 processing username pafonsob
Index 644 processing username patriciapagi
Index 645 processing username daviaraujomiauh
Index 646 processing username gustavo629149
Index 647 processing username elouiselopes
Index 648 processing username batata63
Index 649 processing username janinestella
Index 650 processing username mariosinistro
Index 651 processing username gabslubi
Index 652 processing username fykeda
Index 653 processing username victor_nunes
Index 654 processing username mayloeblein
Index 655 processing username alinestolfi
Index 656 processing username chris-romario
Index 657 processing username perinho
Index 658 processing username queo_ps
Index 659 proces

Index 2135 processing username pedrohenriquecunha
Index 2136 processing username betofigueiredo
Index 2137 processing username otaviozuchini
Index 2138 processing username eschreiner
Index 2139 processing username dreymitosinho
Index 2140 processing username qcronos
Index 2141 processing username marquinreidelas
Index 2142 processing username pedroreis6
Index 2143 processing username sou_noob_ou_pro
Index 2144 processing username luiz2511
Index 2145 processing username yudinakaoka
Index 2146 processing username maciel2801
Index 2147 processing username rudn3i
Index 2148 processing username cookie060680
Index 2149 processing username rafaelfiaes
Index 2150 processing username simonengamaral
Index 2151 processing username elyelrubens
Index 2152 processing username danlok11
Index 2153 processing username gussteph
Index 2154 processing username flaviohe
Index 2155 processing username anabarcellos99
Index 2156 processing username ja0w
Index 2157 processing username renan_jp
Index 2158 proce

Index 3634 processing username cerbero82
Index 3635 processing username sidartasenna
Index 3636 processing username maycongeffer
Index 3637 processing username kasparovo
Index 3638 processing username tadokato
Index 3639 processing username betotau
Index 3640 processing username iurihrs
Index 3641 processing username rafaelribeiro2020
Index 3642 processing username elizangelasilva1
Index 3643 processing username magno164
Index 3644 processing username brunobarross
Index 3645 processing username arturmorandin
Index 3646 processing username calielreis
Index 3647 processing username ta_colla
Index 3648 processing username k4l1d
Index 3649 processing username dinoite
Index 3650 processing username bia3494
Index 3651 processing username olinadesophia
Index 3652 processing username diegonuno
Index 3653 processing username gabrielnovais
Index 3654 processing username johannsebasthianbach
Index 3655 processing username eduocandido
Index 3656 processing username pedroido
Index 3657 processing u

In [10]:
#DENMARK - get player details from DENMARK usernames 
playerdata_DK = get_sample_player_details("DK")
player_DK_df = get_player_dataframe(playerdata_DK)
output_data_players_DK = 'output_data/player_details_DK.csv'
player_DK_df.to_csv(output_data_players_DK, index=True, index_label="player_index")

5000 is the sample size of DK population (20806)

Index 0 fetching player data for player mejlvang92
Index 1 fetching player data for player nymann70
Index 2 fetching player data for player mkors
Index 3 fetching player data for player nicolaipadmesh
Index 4 fetching player data for player gabiboeskov
Index 5 fetching player data for player dawsoncph
Index 6 fetching player data for player checkerddude
Index 7 fetching player data for player tsst
Index 8 fetching player data for player mariusakselwriedt
Index 9 fetching player data for player samassy
Index 10 fetching player data for player julle7742
Index 11 fetching player data for player magnuspaludan
Index 12 fetching player data for player heytigerhere
Index 13 fetching player data for player kriscojr
Index 14 fetching player data for player linde97
Index 15 fetching player data for player cappercapper
Index 16 fetching player data for player adambioue
Index 17 fetching player data for player lillerasmus
Index 18 fetching player d

Index 157 fetching player data for player schjerning
Index 158 fetching player data for player phissen
Index 159 fetching player data for player olahyesman
Index 160 fetching player data for player kararo
Index 161 fetching player data for player sopraninosax
Index 162 fetching player data for player skakrasmus
Index 163 fetching player data for player zelladan
Index 164 fetching player data for player hanserich
Index 165 fetching player data for player kapablak
Index 166 fetching player data for player glistrup118
Index 167 fetching player data for player skovgrisen
Index 168 fetching player data for player ithamos
Index 169 fetching player data for player skonnord
Index 170 fetching player data for player kk04
Index 171 fetching player data for player mattybordo
Index 172 fetching player data for player mgadegaard
Index 173 fetching player data for player mbornholm
Index 174 fetching player data for player spinallah
Index 175 fetching player data for player villadsnolsoe
Index 176 fe

Index 314 fetching player data for player esben987
Index 315 fetching player data for player better2021
Index 316 fetching player data for player baronvongello
Index 317 fetching player data for player jonlind64
Index 318 fetching player data for player simpdani
Index 319 fetching player data for player steend0
Index 320 fetching player data for player dzllz
Index 321 fetching player data for player skakliosis
Index 322 fetching player data for player mattepojken
Index 323 fetching player data for player chesstranslator
Index 324 fetching player data for player marcusholtfuttrup
Index 325 fetching player data for player patagarrouch
Index 326 fetching player data for player madschristensen
Index 327 fetching player data for player poitrpietrov
Index 328 fetching player data for player savorygarbage
Index 329 fetching player data for player jjsteiniche
Index 330 fetching player data for player malmgren
Index 331 fetching player data for player emma308
Index 332 fetching player data for 

Index 471 fetching player data for player kokinshu
Index 472 fetching player data for player jm256
Index 473 fetching player data for player hrcool
Index 474 fetching player data for player georgitsvetanov
Index 475 fetching player data for player jonmichelsen
Index 476 fetching player data for player dontt0
Index 477 fetching player data for player jonasnfh
Index 478 fetching player data for player chessjay77
Index 479 fetching player data for player jensjacobprasse
Index 480 fetching player data for player tommy25113
Index 481 fetching player data for player milanfrost
Index 482 fetching player data for player zretty
Index 483 fetching player data for player spar67
Index 484 fetching player data for player peterjoergensen
Index 485 fetching player data for player 1moak1
Index 486 fetching player data for player dreamingspace
Index 487 fetching player data for player moniqueersaj
Index 488 fetching player data for player mikkelrathsach
Index 489 fetching player data for player markbin

Index 626 fetching player data for player hkh-kasper
Index 627 fetching player data for player calmalev
Index 628 fetching player data for player eucarya
Index 629 fetching player data for player theo2trappy
Index 630 fetching player data for player joe1911
Index 631 fetching player data for player antonperepelitsa
Index 632 fetching player data for player prebenmadsen1
Index 633 fetching player data for player marcchristensen86
Index 634 fetching player data for player 41129
Index 635 fetching player data for player toyhytgjuhhju
Index 636 fetching player data for player rbn2212
Index 637 fetching player data for player parylewicz
Index 638 fetching player data for player joachimfosgaard
Index 639 fetching player data for player rallethor
Index 640 fetching player data for player mrjoejoke
Index 641 fetching player data for player bunudonk
Index 642 fetching player data for player cleverdogg
Index 643 fetching player data for player 1_noahw
Index 644 fetching player data for player to

...

Index 4931 fetching player data for player fq9
Index 4932 fetching player data for player thehorseonc3
Index 4933 fetching player data for player mulder25
Index 4934 fetching player data for player sifgammelgaard
Index 4935 fetching player data for player frandsen1604
Index 4936 fetching player data for player djaymes
Index 4937 fetching player data for player beeden
Index 4938 fetching player data for player fried96
Index 4939 fetching player data for player graabaek
Index 4940 fetching player data for player patraopedro
Index 4941 fetching player data for player maskinmesteren
Index 4942 fetching player data for player dunkemand
Index 4943 fetching player data for player abananna2515464
Index 4944 fetching player data for player august8182
Index 4945 fetching player data for player alkemade98
Index 4946 fetching player data for player madsalnor
Index 4947 fetching player data for player marcusjes
Index 4948 fetching player data for player flemmingknudsen
Index 4949 fetching player da

Index 1602 processing username peterthinggaard
Index 1603 processing username soerendenmark
Index 1604 processing username fredsc8
Index 1605 processing username benjamintrelborgk
Index 1606 processing username ombudsmanden
Index 1607 processing username fried96
Index 1608 processing username dkjensen
Index 1609 processing username hcits
Index 1610 processing username redissen
Index 1611 processing username ftter
Index 1612 processing username brenzius
Index 1613 processing username josephine236453
Index 1614 processing username fredvaeremeddet
Index 1615 processing username lungona93
Index 1616 processing username kageen
Index 1617 processing username magtsa
Index 1618 processing username rasxel
Index 1619 processing username schneekloth
Index 1620 processing username christofferholmstrm
Index 1621 processing username marcosindberg31
Index 1622 processing username marcusffh
Index 1623 processing username lizette9000
Index 1624 processing username julius1507
Index 1625 processing usern

Index 2601 processing username funjazzy
Index 2602 processing username kingcarrot78
Index 2603 processing username noobloadpwn
Index 2604 processing username alavnader123
Index 2605 processing username tryhardbatman
Index 2606 processing username andreidarie
Index 2607 processing username jevper
Index 2608 processing username lykke-per
Index 2609 processing username karlemilsh
Index 2610 processing username bh1906
Index 2611 processing username anders0405
Index 2612 processing username mathiasbo
Index 2613 processing username andersstrom
Index 2614 processing username dual1
Index 2615 processing username hellescheuer
Index 2616 processing username maroni87
Index 2617 processing username rasand100
Index 2618 processing username yukselosman64
Index 2619 processing username imbaonic
Index 2620 processing username jernstangen
Index 2621 processing username rlc252829
Index 2622 processing username iamjevgen007
Index 2623 processing username kasperdahl
Index 2624 processing username mortenhp

Index 3601 processing username antonattacks
Index 3602 processing username kodacck
Index 3603 processing username eslego
Index 3604 processing username a-l-o
Index 3605 processing username puntervold
Index 3606 processing username sullabulla
Index 3607 processing username johanneskristensen
Index 3608 processing username simon5020
Index 3609 processing username melling2003
Index 3610 processing username b3nn0r
Index 3611 processing username mebasic
Index 3612 processing username illummusen
Index 3613 processing username 2581
Index 3614 processing username asddk
Index 3615 processing username tomasz196444
Index 3616 processing username detdafreddy
Index 3617 processing username victorjtc
Index 3618 processing username louiesunde
Index 3619 processing username fossum2712
Index 3620 processing username joffyman
Index 3621 processing username louiisep
Index 3622 processing username magnustschenka
Index 3623 processing username christiandam
Index 3624 processing username jumojamo
Index 3625

Index 4933 processing username mulder25
Index 4934 processing username sifgammelgaard
Index 4935 processing username frandsen1604
Index 4936 processing username djaymes
Index 4937 processing username beeden
Index 4938 processing username fried96
Index 4939 processing username graabaek
Index 4940 processing username patraopedro
Index 4941 processing username maskinmesteren
Index 4942 processing username dunkemand
Index 4943 processing username abananna2515464
Index 4944 processing username august8182
Index 4945 processing username alkemade98
Index 4946 processing username madsalnor
Index 4947 processing username marcusjes
Index 4948 processing username flemmingknudsen
Index 4949 processing username morraband
Index 4950 processing username x17particle
Index 4951 processing username christiandam
Index 4952 processing username ben1993
Index 4953 processing username ericmiguel123
Index 4954 processing username farlas
Index 4955 processing username mikkelmoeller02
Index 4956 processing usern